In [10]:
%reload_kedro

[05/10/24 16:28:02] INFO     Resolved project path as:                                              ]8;id=351915;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py\__init__.py]8;;\:]8;id=36833;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py#164\164]8;;\
                             C:\Users\9509298u\Documents\GitHub\OC_Projects\ocp7-scoring-model-clou                
                             d.                                                                                    
                             To set a different path, run '%reload_kedro <project_root>'                           

                    INFO     Registering new custom resolver: 'km.random_name'                    ]8;id=541183;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro_mlflow\framework\hooks\mlflow_hook.py\mlflow_hook.py]8;;\:]8;id=967889;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro_mlflow\framework\hooks\mlflow_hook.py#65\65]8;;\

                    INFO     The 'tracking_uri' key in mlflow.yml is relative            ]8;id=659575;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro_mlflow\config\kedro_mlflow_config.py\kedro_mlflow_config.py]8;;\:]8;id=403359;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro_mlflow\config\kedro_mlflow_config.py#260\260]8;;\
                             ('server.mlflow_(tracking|registry)_uri = mlruns'). It is                             
                             converted to a valid uri:                                                             
                             'file:///C:/Users/9509298u/Documents/GitHub/OC_Projects/ocp                           
                             7-scoring-model-cloud/mlruns'                                                         

                    INFO     Kedro project ocp7_scoring_model_cloud                                 ]8;id=913493;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py\__init__.py]8;;\:]8;id=619486;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py#134\134]8;;\

                    INFO     Defined global variable 'context', 'session', 'catalog' and            ]8;id=142611;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py\__init__.py]8;;\:]8;id=683891;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py#135\135]8;;\
                             'pipelines'                                                                           

                    INFO     Registered line magic 'run_viz'                                        ]8;id=684861;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py\__init__.py]8;;\:]8;id=511139;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\ipython\__init__.py#141\141]8;;\

In [14]:
import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, roc_curve
from sklearn.model_selection import StratifiedKFold, cross_val_predict

import matplotlib.pyplot as plt

import mlflow

In [11]:
train_df = catalog.load("full_df_train")
#test_df = catalog.load("full_df_test")

[05/10/24 16:28:09] INFO     Loading data from full_df_train (ParquetDataset)...                ]8;id=487264;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\io\data_catalog.py\data_catalog.py]8;;\:]8;id=82391;file://C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\kedro\io\data_catalog.py#483\483]8;;\

In [16]:
def split_data(df, train_size=0.8, test_size=0.2, random_state=42):
    features = [f for f in df.columns if f not in ["SK_ID_CURR", "TARGET"]]
    X = df[features] # Features
    y = df["TARGET"]  # Target variable
    X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=train_size, test_size=test_size, random_state=random_state)
    return X_train, X_test, y_train, y_test

def train_model(X_train, y_train, model):
    model.fit(X_train, y_train)
    return model

def evaluate_model(X_test, y_test, model):
    y_pred = model.predict_proba(X_test)[:,1]
    roc_auc = roc_auc_score(y_test, y_pred)
    return roc_auc

In [27]:
import mlflow
from sklearn.model_selection import StratifiedKFold, cross_val_predict
from sklearn.metrics import roc_auc_score, roc_curve
import matplotlib.pyplot as plt

def train_and_evaluate_model(X, y, model, model_name, params):
    if mlflow.active_run():
        mlflow.end_run()
    # Start an MLflow run
    with mlflow.start_run(run_name=model_name):
        # Fitting model
        model = model.fit(X, y)
        y_probs = model.predict_proba(X)
        y_scores = y_probs[:, 1]  # get the probability of class 1
        # Compute ROC-AUC
        print("Calculating ROC-AUC score...")
        roc_auc = roc_auc_score(y, y_scores)
        
        # Log parameters, metrics, and model
        print("Logging parameters, metrics, and model with MLflow...")
        mlflow.log_params(params)
        mlflow.log_metric("ROC_AUC", roc_auc)
        mlflow.sklearn.log_model(model, "model")

        # Plot ROC curve and save as an artifact
        print("Plotting ROC curve...")
        fpr, tpr, _ = roc_curve(y, y_scores)
        fig = plt.figure(figsize=(6,6))
        plt.plot(fpr, tpr, label='ROC curve (area = %0.2f)' % roc_auc)
        plt.plot([0, 1], [0, 1], 'k--')
        plt.xlim([0.0, 1.0])
        plt.ylim([0.0, 1.05])
        plt.xlabel('False Positive Rate')
        plt.ylabel('True Positive Rate')
        plt.title('Receiver Operating Characteristic')
        plt.legend(loc="lower right")
        roc_curve_path = "roc_curve.png"
        plt.savefig(roc_curve_path)
        plt.close(fig)
        print("Saving ROC curve as an artifact...")
        mlflow.log_artifact(roc_curve_path)

        print("Training and evaluation completed.")
        return roc_auc


In [23]:
mlflow.set_tracking_uri("mlruns")


2024/05/10 16:51:11 INFO mlflow.tracking.fluent: Experiment with name 'OCP7_modelisation_090524_sample5' does not exist. Creating a new experiment.


<Experiment: artifact_location='file:///C:/Users/9509298u/Documents/GitHub/OC_Projects/ocp7-scoring-model-cloud/notebooks/mlruns/218322275285935902', creation_time=1715352671324, experiment_id='218322275285935902', last_update_time=1715352671324, lifecycle_stage='active', name='OCP7_modelisation_090524_sample5', tags={}>

In [29]:
mlflow.set_experiment("OCP7_modelisation_090524_sample6")
from sklearn.ensemble import RandomForestClassifier
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression
import lightgbm as lgb

# Define your dataset
X_train, X_test, y_train, y_test = split_data(train_df.sample(frac=0.5))

# Dummy classifier

params_dummy = {'strategy': 'stratified'}
model_dummy = DummyClassifier(**params_dummy)
train_and_evaluate_model(X_train, y_train, model_dummy, "Dummy Classifier", params_dummy)

# Random Forest
params_rf = {'n_estimators': 50, 'max_depth': 10}
model_rf = RandomForestClassifier(**params_rf)
train_and_evaluate_model(X_train, y_train, model_rf, "Random Forest", params_rf)

# Logistic Regression
params_lr = {'C': 0.1}
model_lr = LogisticRegression(**params_lr)
train_and_evaluate_model(X_train, y_train, model_lr, "Logistic Regression", params_lr)

# LightGBM

params_lgb = {
    'boosting_type': 'gbdt',
    'objective': 'binary',
    'metric': 'auc',
    'num_leaves': 31,
    'learning_rate': 0.05,
    'feature_fraction': 0.9,
    'bagging_fraction': 0.8,
    'bagging_freq': 5,
    'verbose': 1
}

model_lgb = lgb.LGBMClassifier(**params_lgb)
train_and_evaluate_model(X=X_train, y=y_train, model=model_lgb, model_name="LightGBM", params=params_lgb)

Calculating ROC-AUC score...
Logging parameters, metrics, and model with MLflow...
Plotting ROC curve...
Saving ROC curve as an artifact...
Training and evaluation completed.
Calculating ROC-AUC score...
Logging parameters, metrics, and model with MLflow...
Plotting ROC curve...
Saving ROC curve as an artifact...
Training and evaluation completed.
Calculating ROC-AUC score...
Logging parameters, metrics, and model with MLflow...
Plotting ROC curve...
Saving ROC curve as an artifact...
Training and evaluation completed.
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[L

0.8242152620270637

On trouve que le modèle LightGBM est le plus performant. On va donc essayer de l'améliorer en utilisant une validation croisée.

In [38]:
from sklearn.model_selection import GridSearchCV

In [48]:
# Create a training and testing dataset
X_train, X_test, y_train, y_test = split_data(train_df, train_size=0.2, test_size=0.8)

In [49]:
params_lgb = {
    'boosting_type': 'gbdt',
    'objective': 'binary',
    'metric': 'auc',
    'n_estimators':10000,
    'verbose': 1
}

param_grid = {
    'num_leaves': [31, 63, 127],  # Reduced from finer increments
    'learning_rate': [0.01, 0.05, 0.1],  # Focus on commonly effective rates
    'min_child_samples': [20, 40],  # Only two options based on prior knowledge
    'reg_alpha': [0, 0.1],  # Limited to very few options
    'reg_lambda': [0, 0.1]  # Limited to very few options
}

model_lgb = lgb.LGBMClassifier(**params_lgb)

In [50]:
grid_search = GridSearchCV(estimator=model_lgb, param_grid=param_grid, cv=5, scoring='roc_auc', verbose=1)

In [51]:
grid_search.fit(X_train, y_train)

Fitting 5 folds for each of 72 candidates, totalling 360 fits
[LightGBM] [Info] Number of positive: 3987, number of negative: 45213
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.061562 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 41875
[LightGBM] [Info] Number of data points in the train set: 49200, number of used features: 441
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.081037 -> initscore=-2.428346
[LightGBM] [Info] Start training from score -2.428346
[LightGBM] [Info] Number of positive: 3988, number of negative: 45213
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.052527 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 41919
[LightGBM] [Info] Number of data points in the train set: 49201, number of used features: 442
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.081055 -> initscore=-2.428095
[L

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:1                                                                                    │
│                                                                                                  │
│ ❱ 1 grid_search.fit(X_train, y_train)                                                            │
│   2                                                                                              │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\base.py:1474 in wrapper                                                                       │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_search.py:970 in fit                                                         │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_search.py:1527 in _run_search                                                │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_search.py:916 in evaluate_candidates                                         │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\utils\parallel.py:67 in __call__                                                              │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\jobli │
│ b\parallel.py:1863 in __call__                                                                   │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\jobli │
│ b\parallel.py:1792 in _get_sequential_output                                                     │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\utils\parallel.py:129 in __call__                                                             │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_validation.py:895 in _fit_and_score                                          │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\light │
│ gbm\sklearn.py:1187 in fit                                                                       │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\light │
│ gbm\sklearn.py:885 in fit                                                                        │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scorin

In [ ]:
print("Best parameters:", grid_search.best_params_)
print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))

In [ ]:
best_model = grid_search.best_estimator_
validation_roc_auc = best_model.score(X_test, y_test)
print("Validation accuracy: {:.2f}".format(validation_roc_auc))

In [52]:
# Perform random search instead
from sklearn.model_selection import RandomizedSearchCV

In [53]:
param_dist = {
    'num_leaves': [31, 62, 127, 255],
    'max_depth': [-1, 5, 10, 20],
    'learning_rate': [0.01, 0.05, 0.1, 0.2],
    'n_estimators': [200, 500],
    'subsample': [0.6, 0.8, 1.0],
    'colsample_bytree': [0.6, 0.8, 1.0],
    'reg_alpha': [0, 0.1],
    'reg_lambda': [0, 0.1]
}


In [54]:
random_search = RandomizedSearchCV(estimator=model_lgb, param_distributions=param_grid, n_iter=10, cv=5, scoring='roc_auc', verbose=1)

In [55]:
random_search.fit(X_train, y_train)

Fitting 5 folds for each of 10 candidates, totalling 50 fits
[LightGBM] [Info] Number of positive: 3987, number of negative: 45213
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.064409 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 41875
[LightGBM] [Info] Number of data points in the train set: 49200, number of used features: 441
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.081037 -> initscore=-2.428346
[LightGBM] [Info] Start training from score -2.428346
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain:

Exception ignored on calling ctypes callback function: <function _log_callback at 0x000001D7838F8AF0>
Traceback (most recent call last):
  File "C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\lightgbm\basic.py", line 224, in _log_callback
    def _log_callback(msg: bytes) -> None:
KeyboardInterrupt: 


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x000001D7A7BA81F0>>
Traceback (most recent call last):
  File "C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\ipykernel\ipkernel.py", line 788, in _clean_thread_parent_frames
    if phase != "start":
KeyboardInterrupt: 


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:1                                                                                    │
│                                                                                                  │
│ ❱ 1 random_search.fit(X_train, y_train)                                                          │
│   2                                                                                              │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\base.py:1474 in wrapper                                                                       │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_search.py:970 in fit                                                         │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_search.py:1914 in _run_search                                                │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_search.py:916 in evaluate_candidates                                         │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\utils\parallel.py:67 in __call__                                                              │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\jobli │
│ b\parallel.py:1863 in __call__                                                                   │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\jobli │
│ b\parallel.py:1792 in _get_sequential_output                                                     │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\utils\parallel.py:129 in __call__                                                             │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\sklea │
│ rn\model_selection\_validation.py:895 in _fit_and_score                                          │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\light │
│ gbm\sklearn.py:1187 in fit                                                                       │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\light │
│ gbm\sklearn.py:885 in fit                                                                        │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scorin

In [ ]:
print("Best parameters found:", random_search.best_params_)
print("Best cross-validation score: {:.2f}".format(random_search.best_score_))
best_model = random_search.best_estimator_
validation_roc_auc = best_model.score(X_test, y_test)
print("Validation accuracy: {:.2f}".format(validation_roc_auc))

In [ ]:
clf = lgb.LGBMClassifier(
            nthread=4,
            n_estimators=10000,
            learning_rate=0.02,
            num_leaves=34,
            colsample_bytree=0.9497036,
            subsample=0.8715623,
            max_depth=8,
            reg_alpha=0.041545473,
            reg_lambda=0.0735294,
            min_split_gain=0.0222415,
            min_child_weight=39.3259775,
            silent=-1,
            verbose=-1, )

In [30]:
# Create a training and testing dataset
X_train, X_test, y_train, y_test = split_data(train_df)
train_set = lgb.Dataset(data = X_train, label = y_train)
test_set = lgb.Dataset(data = X_test, label = y_test)

In [31]:
# Get default hyperparameters
model = lgb.LGBMClassifier()
default_params = model.get_params()

In [32]:
default_params


{
    'boosting_type': 'gbdt',
    'class_weight': None,
    'colsample_bytree': 1.0,
    'importance_type': 'split',
    'learning_rate': 0.1,
    'max_depth': -1,
    'min_child_samples': 20,
    'min_child_weight': 0.001,
    'min_split_gain': 0.0,
    'n_estimators': 100,
    'n_jobs': None,
    'num_leaves': 31,
    'objective': None,
    'random_state': None,
    'reg_alpha': 0.0,
    'reg_lambda': 0.0,
    'subsample': 1.0,
    'subsample_for_bin': 200000,
    'subsample_freq': 0
}

In [33]:
# Remove the number of estimators because we set this to 10000 in the cv call
del default_params['n_estimators']

In [36]:
# Cross validation with early stopping
N_FOLDS = 5
MAX_EVALS = 5
cv_results = lgb.cv(default_params, train_set, num_boost_round = 10000, 
                    metrics = 'auc', nfold = N_FOLDS, seed = 42)

[LightGBM] [Warning] Unknown parameter: importance_type
[LightGBM] [Warning] Unknown parameter: importance_type
[LightGBM] [Warning] Unknown parameter: importance_type
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.206111 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 45280
[LightGBM] [Info] Number of data points in the train set: 196804, number of used features: 456
[LightGBM] [Warning] Unknown parameter: importance_type
[LightGBM] [Warning] Unknown parameter: importance_type
[LightGBM] [Warning] Unknown parameter: importance_type
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.176241 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 45280
[LightGBM] [Info] Number of data points in the train set: 196804, number of used features: 456
[LightGBM] [Warning] Unknown parameter: importance_type
[LightGBM] [Warning] Unk

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:4                                                                                    │
│                                                                                                  │
│   1 # Cross validation with early stopping                                                       │
│   2 N_FOLDS = 5                                                                                  │
│   3 MAX_EVALS = 5                                                                                │
│ ❱ 4 cv_results = lgb.cv(default_params, train_set, num_boost_round = 10000,                      │
│   5 │   │   │   │   │   metrics = 'auc', nfold = N_FOLDS, seed = 42)                             │
│   6                                                                                              │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\light │
│ gbm\engine.py:761 in cv                                                                          │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\light │
│ gbm\engine.py:363 in handler_function                                                            │
│                                                                                                  │
│ C:\Users\9509298u\AppData\Local\miniconda3\envs\ocp7-scoring-model-cloud\lib\site-packages\light │
│ gbm\basic.py:3891 in update                                                                      │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
KeyboardInterrupt

In [ ]:
def kfold_lightgbm(df, num_folds):
    # Divide in training/validation and test data
    train_df = df[df['TARGET'].notnull()]
    test_df = df[df['TARGET'].isnull()]
    print("Starting LightGBM. Train shape: {}, test shape: {}".format(train_df.shape, test_df.shape))
    # Cross validation model
    folds = StratifiedKFold(n_splits= num_folds, shuffle=True, random_state=1001)
    # Create arrays and dataframes to store results
    oof_preds = np.zeros(train_df.shape[0])
    sub_preds = np.zeros(test_df.shape[0])
    feature_importance_df = pd.DataFrame()
    feats = [f for f in train_df.columns if f not in ['TARGET','SK_ID_CURR','SK_ID_BUREAU','SK_ID_PREV','index']]
    
    for n_fold, (train_idx, valid_idx) in enumerate(folds.split(train_df[feats], train_df['TARGET'])):
        train_x, train_y = train_df[feats].iloc[train_idx], train_df['TARGET'].iloc[train_idx]
        valid_x, valid_y = train_df[feats].iloc[valid_idx], train_df['TARGET'].iloc[valid_idx]

        # LightGBM parameters found by Bayesian optimization
        clf = lgb.LGBMClassifier(
            nthread=4,
            n_estimators=10000,
            learning_rate=0.02,
            num_leaves=34,
            colsample_bytree=0.9497036,
            subsample=0.8715623,
            max_depth=8,
            reg_alpha=0.041545473,
            reg_lambda=0.0735294,
            min_split_gain=0.0222415,
            min_child_weight=39.3259775,
            silent=-1,
            verbose=-1, )

        clf.fit(train_x, train_y, eval_set=[(train_x, train_y), (valid_x, valid_y)], 
            eval_metric= 'auc', verbose= 200, early_stopping_rounds= 200)

        oof_preds[valid_idx] = clf.predict_proba(valid_x, num_iteration=clf.best_iteration_)[:, 1]
        sub_preds += clf.predict_proba(test_df[feats], num_iteration=clf.best_iteration_)[:, 1] / folds.n_splits

        fold_importance_df = pd.DataFrame()
        fold_importance_df["feature"] = feats
        fold_importance_df["importance"] = clf.feature_importances_
        fold_importance_df["fold"] = n_fold + 1
        feature_importance_df = pd.concat([feature_importance_df, fold_importance_df], axis=0)
        print('Fold %2d AUC : %.6f' % (n_fold + 1, roc_auc_score(valid_y, oof_preds[valid_idx])))
        del clf, train_x, train_y, valid_x, valid_y
        
    print('Full AUC score %.6f' % roc_auc_score(train_df['TARGET'], oof_preds))
    # Write submission file and plot feature importance
    return feature_importance_df